This script is EDA for scraping NYC zoning and regulation data from the planning.nyc.gov website. In the end, I'd like to create a research tool for NYC zoning and regulation and perhaps a search engine to help developers and policy makers find the appropriate piece of legistation.

For now, we can create a structure table to collect all the data, but then we are going to have to create some type of strucutre to process the data in a meaningful way. For example, for one article there might be multiple chapters and in those chapters certain itmes might not be broken down but instead in one large text. This type of text data needs to be organize and filtered somehow.

In [1]:
# Libraries
import requests
import urllib.request
import time
from bs4 import BeautifulSoup
import pandas as pd
import re

# Regex remove new line breaks when getting text
regex = re.compile(r'\n', re.IGNORECASE)

# URL link for NYC zoning
url = 'https://zr.planning.nyc.gov'
response = requests.get(url)

# parameters
article_parameter = '/article-'

columns = ['State', 'City','Article_Number', 'Article_Link', 'Article_Text', 'Chapter_Number', 'Chapter_Link', 'Chapter_Text']

df = pd.DataFrame(columns = columns)

# BS
soup = BeautifulSoup(response.text, "html.parser")

# Finds all article tags in the HTML
articleHTML = soup.findAll('article')

# Loops to collect all the article links
for i in range(len(articleHTML)):
    
    # Find all articles
    one_article_tag = soup.findAll('a')[i]
    
    # Find all href articles
    link = one_article_tag['href']
    
    # Make sure we are only collecting article related data
    if(link.find(article_parameter) >= 0):
        
        # chapter parameter
        chapter_parameter =  link + '/chapter-'

        # get article text
        article_text = one_article_tag.find('div', attrs = {'class': 'field field--name-field-article-title field--type-string field--label-hidden field__item'})

        #  find the chapters
        url_article =  url + link
        response_chapter = requests.get(url_article)
        soup_chapter = BeautifulSoup(response_chapter.text, "html.parser")
        chapterHTML = soup_chapter.find('div', attrs = {'class': 'article-chapters'}).find('div', attrs = {'class': 'view-content'}).findAll('div', attrs = {'class': 'views-row'})
        
        # traverse through chapters
        for j in range(len(chapterHTML)):
            
            # list of chapters
            one_chapter_tag = chapterHTML[j]
            
            # chapter link at position 0 of the "a" tag
            link_chapter = one_chapter_tag.findAll('a')[0]['href']
            
            # Chapter text is the next sibling after span
            chapter_text = one_chapter_tag.find('span', attrs = {'class': 'field field--name-title field--type-string field--label-hidden'}).next_sibling
            
            # Replace new lines ('\n') with blank spaces
            chapter_text = re.sub(regex, '', chapter_text)
        
            if(link_chapter.find(chapter_parameter) >= 0):
            
                # populate table with article and chapters
                df = df.append({
                'Article_Number': link,
                'Article_Link': url_article,
                'Article_Text': article_text.text,
                'Chapter_Number': link_chapter,
                'Chapter_Link': url_article + link_chapter,
                'Chapter_Text': chapter_text
            }, ignore_index = True)

# Adds state and city column
df['State'] = 'NY'
df['City'] = 'NYC'


In [2]:
df.head()

State City Article_Number                           Article_Link  \
0    NY  NYC     /article-i  https://zr.planning.nyc.gov/article-i   
1    NY  NYC     /article-i  https://zr.planning.nyc.gov/article-i   
2    NY  NYC     /article-i  https://zr.planning.nyc.gov/article-i   
3    NY  NYC     /article-i  https://zr.planning.nyc.gov/article-i   
4    NY  NYC     /article-i  https://zr.planning.nyc.gov/article-i   

         Article_Text        Chapter_Number  \
0  General Provisions  /article-i/chapter-1   
1  General Provisions  /article-i/chapter-2   
2  General Provisions  /article-i/chapter-3   
3  General Provisions  /article-i/chapter-4   
4  General Provisions  /article-i/chapter-5   

                                        Chapter_Link  \
0  https://zr.planning.nyc.gov/article-i/article-...   
1  https://zr.planning.nyc.gov/article-i/article-...   
2  https://zr.planning.nyc.gov/article-i/article-...   
3  https://zr.planning.nyc.gov/article-i/article-...   
4  https://zr.planning.nyc.gov/article-i/article-...   

                                        Chapter_Text  
0   - Title, Establishment of Controls and Interp...  
1         - Construction of Language and Definitions  
2   - Comprehensive Off-street Parking and Loadin...  
3                        - Sidewalk Cafe Regulations  
4   - Residential Conversion within Existing Buil...

In [36]:
# version 2 to include chapter text

# Libraries
import requests
import urllib.request
import time
from bs4 import BeautifulSoup
import pandas as pd
import re

# Regex remove new line breaks when getting text
regex = re.compile(r'\n', re.IGNORECASE)

# URL link for NYC zoning
url = 'https://zr.planning.nyc.gov'
response = requests.get(url)

# parameters
article_parameter = '/article-'

columns = ['State', 'City','Article_Number', 'Article_Link', 'Article_Text',
           'Chapter_Number', 'Chapter_Link', 'Chapter_Text', 'Section_Title',
           'Section_Number','Section_Link', 'Section_Child_Title', 'Section_Child_Link', 
           'Section_Child_Text']

df = pd.DataFrame(columns = columns)

# BS
soup = BeautifulSoup(response.text, "html.parser")

# Finds all article tags in the HTML
articleHTML = soup.findAll('article')

# loops to collect all the article links
for i in range(len(articleHTML)):
    
    # find all articles
    one_article_tag = soup.findAll('a')[i]
    
    # find all href articles
    link = one_article_tag['href']
    
    # Make sure we are only collecting article related data
    if(link.find(article_parameter) >= 0):
        
        # chapter parameter
        chapter_parameter =  link + '/chapter-'

        # get article text
        article_text = one_article_tag.find('div', attrs = {'class': 'field field--name-field-article-title field--type-string field--label-hidden field__item'})
        #  find the chapters
        url_article =  url + link
        response_chapter = requests.get(url_article)
        soup_chapter = BeautifulSoup(response_chapter.text, "html.parser")
        chapterHTML = soup_chapter.find('div', attrs = {'class': 'article-chapters'}).find('div', attrs = {'class': 'view-content'}).findAll('div', attrs = {'class': 'views-row'})
        
        # traverse through chapters
        for j in range(len(chapterHTML)):
            
            # list of chapters
            one_chapter_tag = chapterHTML[j]
            
            # chapter link at position 0 of the "a" tag
            link_chapter = one_chapter_tag.findAll('a')[0]['href']
            
            # chapter text is the next sibling after span
            chapter_text = one_chapter_tag.find('span', attrs = {'class': 'field field--name-title field--type-string field--label-hidden'}).next_sibling
            
            # replace new lines ('\n') with blank spaces
            chapter_text = re.sub(regex, '', chapter_text)
        
            if(link_chapter.find(chapter_parameter) >= 0):
                
                # section parameter
                url_section = url + link_chapter
                response_section = requests.get(url_section)
                soup_section = BeautifulSoup(response_section.text, "html.parser")
                sectionHTML = soup_section.find('div', attrs = {'class': 'chapter-sections'}).find('div', attrs = {'class': 'view-content'}).findAll('div', attrs = {'class': 'views-row'})
                print(len(sectionHTML))
                
                # traverse through section chapters "resolution"
                for k in range(len(sectionHTML)):
                    
                    # list of resolutions
                    one_section_tag = sectionHTML[k]
                    print(k)
                    print(one_section_tag)
                    section_title = one_section_tag.find('div', attr = {'class': 'section-title'})
                    section_number = one_section_tag.find('div', attr = {'class': 'section-number'})
                    #section_link = one_section_tag.find('a', attr = {'class': 'section-link'})['href']
                    
                    
                    # populate table with article and chapters
                    df = df.append({
                    'Article_Number': link,
                    'Article_Link': url_article,
                    'Article_Text': article_text.text,
                    'Chapter_Number': link_chapter,
                    'Chapter_Link': url_article + link_chapter,
                    'Chapter_Text': chapter_text,
                    'Section_Title': section_title,
                    'Section_Number': section_number
                }, ignore_index = True)

# Adds state and city column
df['State'] = 'NY'
df['City'] = 'NYC'


53
0
<div class="views-row">
<article about="/article-i/chapter-1/11-00" class="node node--type-section node--view-mode-teaser has-children" data-history-node-id="18414" id="nav-11-00" role="article">
<a class="section-link" data-node-id="18414" data-section-number="11-00" href="#11-00">
<div class="section-number">11-00</div>
<div class="section-title">TITLE</div>
</a>
<div class="section-children" data-children-for="11-00">
<div class="views-element-container"><div class="view view-sections view-id-sections view-display-id-block_5 js-view-dom-id-ae61b5aa865c0878636519263c6dacc4cd75517fdda29eaaf64c6b301fc8799e">
<div class="view-content">
<div class="views-row">
<article about="/article-i/chapter-1/11-01" class="node node--type-section node--view-mode-teaser" data-history-node-id="18415" id="nav-11-01" role="article">
<a class="section-link" data-node-id="18415" data-section-number="11-01" href="#11-01">
<div class="section-number">11-01</div>
<div class="section-title">Long Title</di

17
<div class="views-row">
<article about="/article-i/chapter-1/11-22" class="node node--type-section node--view-mode-teaser" data-history-node-id="18431" id="nav-11-22" role="article">
<a class="section-link" data-node-id="18431" data-section-number="11-22" href="#11-22">
<div class="section-number">11-22</div>
<div class="section-title">Application of Overlapping Regulations</div>
</a>
</article>
</div>
18
<div class="views-row">
<article about="/article-i/chapter-1/11-23" class="node node--type-section node--view-mode-teaser" data-history-node-id="18432" id="nav-11-23" role="article">
<a class="section-link" data-node-id="18432" data-section-number="11-23" href="#11-23">
<div class="section-number">11-23</div>
<div class="section-title">Demolition and Replacement </div>
</a>
</article>
</div>
19
<div class="views-row">
<article about="/article-i/chapter-1/11-25" class="node node--type-section node--view-mode-teaser" data-history-node-id="18433" id="nav-11-25" role="article">
<a clas

42
<div class="views-row">
<article about="/article-i/chapter-1/11-412" class="node node--type-section node--view-mode-teaser" data-history-node-id="18456" id="nav-11-412" role="article">
<a class="section-link" data-node-id="18456" data-section-number="11-412" href="#11-412">
<div class="section-number">11-412</div>
<div class="section-title">Alterations, extensions or enlargements</div>
</a>
</article>
</div>
43
<div class="views-row">
<article about="/article-i/chapter-1/11-413" class="node node--type-section node--view-mode-teaser" data-history-node-id="18457" id="nav-11-413" role="article">
<a class="section-link" data-node-id="18457" data-section-number="11-413" href="#11-413">
<div class="section-number">11-413</div>
<div class="section-title">Change of use</div>
</a>
</article>
</div>
44
<div class="views-row">
<article about="/article-i/chapter-1/11-42" class="node node--type-section node--view-mode-teaser" data-history-node-id="18458" id="nav-11-42" role="article">
<a class="

53
0
<div class="views-row">
<article about="/article-i/chapter-3/13-00" class="node node--type-section node--view-mode-teaser has-children" data-history-node-id="18467" id="nav-13-00" role="article">
<a class="section-link" data-node-id="18467" data-section-number="13-00" href="#13-00">
<div class="section-number">13-00</div>
<div class="section-title">GENERAL PURPOSES</div>
</a>
<div class="section-children" data-children-for="13-00">
<div class="views-element-container"><div class="view view-sections view-id-sections view-display-id-block_5 js-view-dom-id-683022a2ab1867d53d6c88a766ca43f470e05b94a08e941974fe95f20a00f5e3">
<div class="view-content">
<div class="views-row">
<article about="/article-i/chapter-3/13-01" class="node node--type-section node--view-mode-teaser" data-history-node-id="18468" id="nav-13-01" role="article">
<a class="section-link" data-node-id="18468" data-section-number="13-01" href="#13-01">
<div class="section-number">13-01</div>
<div class="section-title">Gen

17
<div class="views-row">
<article about="/article-i/chapter-3/13-141" class="node node--type-section node--view-mode-teaser" data-history-node-id="18484" id="nav-13-141" role="article">
<a class="section-link" data-node-id="18484" data-section-number="13-141" href="#13-141">
<div class="section-number">13-141</div>
<div class="section-title">Areas where public parking lots are not permitted</div>
</a>
</article>
</div>
18
<div class="views-row">
<article about="/article-i/chapter-3/13-15" class="node node--type-section node--view-mode-teaser" data-history-node-id="18485" id="nav-13-15" role="article">
<a class="section-link" data-node-id="18485" data-section-number="13-15" href="#13-15">
<div class="section-number">13-15</div>
<div class="section-title">Permitted Parking for Automobile Rental Establishments</div>
</a>
</article>
</div>
19
<div class="views-row">
<article about="/article-i/chapter-3/13-16" class="node node--type-section node--view-mode-teaser" data-history-node-id="18

...

25
<div class="views-row">
<article about="/article-xiii/chapter-8/138-40" class="node node--type-section node--view-mode-teaser has-children" data-history-node-id="20241" id="nav-138-40" role="article">
<a class="section-link" data-node-id="20241" data-section-number="138-40" href="#138-40">
<div class="section-number">138-40</div>
<div class="section-title">OFF-STREET PARKING AND LOADING REGULATIONS</div>
</a>
<div class="section-children" data-children-for="138-40">
<div class="views-element-container"><div class="view view-sections view-id-sections view-display-id-block_5 js-view-dom-id-23fa8addae97aff09d5a4a15beb54b5b50606be4e898d62cb0a0dcc296d5df95">
<div class="view-content">
<div class="views-row">
<article about="/article-xiii/chapter-8/138-41" class="node node--type-section node--view-mode-teaser" data-history-node-id="20242" id="nav-138-41" role="article">
<a class="section-link" data-node-id="20242" data-section-number="138-41" href="#138-41">
<div class="section-number">13

11
<div class="views-row">
<article about="/article-xiv/chapter-1/141-22" class="node node--type-section node--view-mode-teaser" data-history-node-id="20132" id="nav-141-22" role="article">
<a class="section-link" data-node-id="20132" data-section-number="141-22" href="#141-22">
<div class="section-number">141-22</div>
<div class="section-title">Special Floor Area Regulations in R8A Districts</div>
</a>
</article>
</div>
12
<div class="views-row">
<article about="/article-xiv/chapter-1/141-23" class="node node--type-section node--view-mode-teaser" data-history-node-id="20133" id="nav-141-23" role="article">
<a class="section-link" data-node-id="20133" data-section-number="141-23" href="#141-23">
<div class="section-number">141-23</div>
<div class="section-title">Special Height and Setback Regulations Along the Elevated Rail Structure Outside Subdistrict A</div>
</a>
</article>
</div>
13
<div class="views-row">
<article about="/article-xiv/chapter-1/141-24" class="node node--type-sectio

12
<div class="views-row">
<article about="/article-xiv/chapter-2/142-09" class="node node--type-section node--view-mode-teaser" data-history-node-id="20020" id="nav-142-09" role="article">
<a class="section-link" data-node-id="20020" data-section-number="142-09" href="#142-09">
<div class="section-number">142-09</div>
<div class="section-title">Off-street Relocation of Subway Station Entrances</div>
</a>
</article>
</div>
13
<div class="views-row">
<article about="/article-xiv/chapter-2/142-10" class="node node--type-section node--view-mode-teaser has-children" data-history-node-id="20021" id="nav-142-10" role="article">
<a class="section-link" data-node-id="20021" data-section-number="142-10" href="#142-10">
<div class="section-number">142-10</div>
<div class="section-title">SPECIAL USE REGULATIONS</div>
</a>
<div class="section-children" data-children-for="142-10">
<div class="views-element-container"><div class="view view-sections view-id-sections view-display-id-block_5 js-view-do

24
<div class="views-row">
<article about="/article-xiv/chapter-2/142-23" class="node node--type-section node--view-mode-teaser" data-history-node-id="20032" id="nav-142-23" role="article">
<a class="section-link" data-node-id="20032" data-section-number="142-23" href="#142-23">
<div class="section-number">142-23</div>
<div class="section-title">Floor Area Regulations in Subareas B2 and B3</div>
</a>
</article>
</div>
25
<div class="views-row">
<article about="/article-xiv/chapter-2/142-24" class="node node--type-section node--view-mode-teaser" data-history-node-id="20033" id="nav-142-24" role="article">
<a class="section-link" data-node-id="20033" data-section-number="142-24" href="#142-24">
<div class="section-number">142-24</div>
<div class="section-title">Floor Area Regulations in Subdistrict D</div>
</a>
</article>
</div>
26
<div class="views-row">
<article about="/article-xiv/chapter-2/142-30" class="node node--type-section node--view-mode-teaser" data-history-node-id="20034" id=

36
<div class="views-row">
<article about="/article-xiv/chapter-2/142-49" class="node node--type-section node--view-mode-teaser has-children" data-history-node-id="20044" id="nav-142-49" role="article">
<a class="section-link" data-node-id="20044" data-section-number="142-49" href="#142-49">
<div class="section-number">142-49</div>
<div class="section-title">Height and Setback for Certain Zoning Lots in Subdistricts C and D</div>
</a>
<div class="section-children" data-children-for="142-49">
<div class="views-element-container"><div class="view view-sections view-id-sections view-display-id-block_5 js-view-dom-id-7bd4b5b33d3a4a32b9b96108682802cccbda39ae716d5ccc605a801ca927aaad">
<div class="view-content">
<div class="views-row">
<article about="/article-xiv/chapter-2/142-491" class="node node--type-section node--view-mode-teaser" data-history-node-id="20045" id="nav-142-491" role="article">
<a class="section-link" data-node-id="20045" data-section-number="142-491" href="#142-491">
<div

In [37]:
df.head()

State City Article_Number                           Article_Link  \
0    NY  NYC     /article-i  https://zr.planning.nyc.gov/article-i   
1    NY  NYC     /article-i  https://zr.planning.nyc.gov/article-i   
2    NY  NYC     /article-i  https://zr.planning.nyc.gov/article-i   
3    NY  NYC     /article-i  https://zr.planning.nyc.gov/article-i   
4    NY  NYC     /article-i  https://zr.planning.nyc.gov/article-i   

         Article_Text        Chapter_Number  \
0  General Provisions  /article-i/chapter-1   
1  General Provisions  /article-i/chapter-1   
2  General Provisions  /article-i/chapter-1   
3  General Provisions  /article-i/chapter-1   
4  General Provisions  /article-i/chapter-1   

                                        Chapter_Link  \
0  https://zr.planning.nyc.gov/article-i/article-...   
1  https://zr.planning.nyc.gov/article-i/article-...   
2  https://zr.planning.nyc.gov/article-i/article-...   
3  https://zr.planning.nyc.gov/article-i/article-...   
4  https://zr.planning.nyc.gov/article-i/article-...   

                                        Chapter_Text Section_Title  \
0   - Title, Establishment of Controls and Interp...          None   
1   - Title, Establishment of Controls and Interp...          None   
2   - Title, Establishment of Controls and Interp...          None   
3   - Title, Establishment of Controls and Interp...          None   
4   - Title, Establishment of Controls and Interp...          None   

  Section_Number Section_Link Section_Child_Title Section_Child_Link  \
0           None          NaN                 NaN                NaN   
1           None          NaN                 NaN                NaN   
2           None          NaN                 NaN                NaN   
3           None          NaN                 NaN                NaN   
4           None          NaN                 NaN                NaN   

  Section_Child_Text  
0                NaN  
1                NaN  
2                NaN  
3                NaN  
4                NaN

In [57]:
# workingon chapters
url = 'https://zr.planning.nyc.gov/article-i'

response = requests.get(url)

soup = BeautifulSoup(response.text, "html.parser")

test = soup.find('div', attrs = {'class': 'article-chapters'}).find('div', attrs = {'class': 'view-content'}).findAll('div', attrs = {'class': 'views-row'})

len(test)
#test2 = test[1]
#test2.findAll('a')[0]['href']

6

In [62]:
regex = re.compile(r'/n', re.IGNORECASE)
link = '/article-i'
url_article =  url + link
response_chapter = requests.get(url_article)
soup_chapter = BeautifulSoup(response_chapter.text, "html.parser")
# need to fix the soup_chapter.find
chapterHTML = soup_chapter.find('div', attrs = {'class': 'article-chapters'}).find('div', attrs = {'class': 'view-content'}).findAll('div', attrs = {'class': 'views-row'})

chapterHTML = chapterHTML[5]

chapter_text = chapterHTML.find('span', attrs = {'class': 'field field--name-title field--type-string field--label-hidden'}).next_sibling

chapter_text = re.sub(regex, '', chapter_text)
print(chapter_text)

chapterHTML


 - Comprehensive Off-street Parking Regulations in the Long Island City Area


<div class="views-row">
<article about="/article-i/chapter-6" class="node node--type-chapter node--view-mode-leftnav" data-history-node-id="85" role="article">
<a class="chapter-title" href="/article-i/chapter-6"><span class="field field--name-title field--type-string field--label-hidden">Chapter 6</span>
 - Comprehensive Off-street Parking Regulations in the Long Island City Area</a>
</article>
</div>

In [4]:
<div class="ch-fig">
                        <div class="fig-title">The City of New York</div>
                        <div class="fig-name">Bill de Blasio, Mayor</div>
                    </div>

IndentationError: unindent does not match any outer indentation level (<tokenize>, line 4)